In [1]:
import pyodbc
import configparser
import pandas as pd
import numpy as np 
from datetime import datetime, time

In [2]:
config = configparser.ConfigParser()
config.read(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\CODIGOS\relatório_improdutivo\credenciais.ini")


['C:\\Users\\joao.herculano\\GRUPO GINSENG\\Assistência Suprimentos - 2025\\CODIGOS\\relatório_improdutivo\\credenciais.ini']

In [3]:

conn = pyodbc.connect(
    f"DRIVER={{SQL Server}};"
    f"SERVER={config['banco']['host']},1433;"
    f"DATABASE=GINSENG;"
    f"UID={config['banco']['user']};"
    f"PWD={config['banco']['password']}")


# 1. Puxa fne_pdv (já filtrado)
query_fne = """
SELECT
    fne.cnpj_destinatario,
    fne.cnf AS Nota_Fiscal,
    CAST(fne.data_emissao AS date) AS data_emissao,
    fnei.codigo_pedido,
    fnei.n_item,
    fnei.cod_produto,
    fnei.produto,
    fnei.quantidade,
    fnei.valor_unitario,
    fnei.valor_total_produtos,
    b.PDV
FROM fato_notas_entrada fne
INNER JOIN fato_notas_entrada_itens fnei ON fne.chave = fnei.chave
INNER JOIN base_pdvs b ON fne.cnpj_destinatario = b.CNPJ
WHERE fne.data_emissao > '2025-07-01'
"""
df_fne = pd.read_sql(query_fne, conn)

query_pedidos = """
SELECT
    sellOrders,
    sku,
    storeCode,
    MAX(quantity_accepted) AS quantity_accepted,
    MAX(status) AS status,
    MAX(pedido_id) AS pedido_id,
    MAX(p.[date]) AS [date],
    MAX(deliveryDate) AS deliveryDate,
    cd.Ciclo 
FROM produtos_pedidos p
INNER JOIN ciclos_data_2025 cd on cd.[Date] = p.[date] and cd.MARCA ='BOT'
GROUP BY sellOrders, sku, storeCode, cd.Ciclo 
"""
df_pedidos = pd.read_sql(query_pedidos, conn)

# 3. Puxa draft
query_draft = """
SELECT loja_id, code, salescurve
FROM draft
"""
df_draft = pd.read_sql(query_draft, conn)

# ---- Fazendo os JOINs e agregações em Pandas ----

# JOIN fne com pedidos
df_join = df_fne.merge(df_pedidos, left_on=['codigo_pedido','cod_produto','PDV'],
                       right_on=['sellOrders','sku','storeCode'], how="inner")

# JOIN com draft
df_join = df_join.merge(df_draft, left_on=['PDV','cod_produto'],
                        right_on=['loja_id','code'], how="inner")

# Agrupamento final
df_result = (
    df_join.groupby(['Ciclo','PDV','cod_produto','pedido_id'])
    .agg(
        data_emissao_nf=('data_emissao','max'),
        data_pedido=('date','max'),
        data_prevista_atendimento=('deliveryDate','max'),
        faturado_industria=('quantidade','sum'),
        quantidade_pedida=('quantity_accepted','max'),
        status=('status','max'),
        salescurve=('salescurve','max'),
        valor_total_produtos=('valor_total_produtos','sum'),
        notas=('Nota_Fiscal', lambda x: ', '.join(sorted(set(x)))),
        pedidos=('codigo_pedido', lambda x: ', '.join(sorted(set(x))))
    )
    .reset_index()
)

# Calculando atendimento
df_result['atendimento'] = (
    df_result['faturado_industria'] / df_result['quantidade_pedida'].replace(0, pd.NA)
).round(2)

df_result.head()

C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_35380\87634967.py:28: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  df_fne = pd.read_sql(query_fne, conn)
C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_35380\87634967.py:45: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  df_pedidos = pd.read_sql(query_pedidos, conn)
C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_35380\87634967.py:52: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  df_draft = pd.read_sql(query_draft, conn)


Ciclo    PDV cod_produto pedido_id data_emissao_nf  \
0  C202507  12522       52757   1515922      2025-07-09   
1  C202507  12817       52757   1515918      2025-07-09   
2  C202507  12817       87066   1517306      2025-07-09   
3  C202507  12818       52757   1515924      2025-07-09   
4  C202507  12820       52757   1515943      2025-07-09   

                   data_pedido    data_prevista_atendimento  \
0  2025-05-22 00:00:00.0000000  2025-06-06 00:00:00.0000000   
1  2025-05-22 00:00:00.0000000  2025-06-06 00:00:00.0000000   
2  2025-05-22 00:00:00.0000000  2025-06-13 00:00:00.0000000   
3  2025-05-22 00:00:00.0000000  2025-06-06 00:00:00.0000000   
4  2025-05-22 00:00:00.0000000  2025-06-06 00:00:00.0000000   

   faturado_industria  quantidade_pedida                 status salescurve  \
0                   5                 35  Parcialmente Atendido          C   
1                  24                 90  Parcialmente Atendido          C   
2                   1                  9              Concluído          C   
3                   4                 25  Parcialmente Atendido          C   
4                   3                 20  Parcialmente Atendido          C   

   valor_total_produtos     notas     pedidos atendimento  
0                 45.36  31953127  0165202706    0.142857  
1                217.71  31754122  0165202491    0.266667  
2                  6.11  31754122  0165206643    0.111111  
3                 36.29  76077782  0165202707        0.16  
4                 27.21  29403846  0165202369        0.15

In [4]:
# Extrair ano e ciclo
df_result['ano'] = df_result['Ciclo'].str[1:5].astype(int)
df_result['num_ciclo'] = df_result['Ciclo'].str[5:].astype(int)

# Calcular ciclo anterior
df_result['ciclo_anterior'] = df_result.apply(
    lambda row: f"C{row['ano']}{row['num_ciclo']-1:02d}" if row['num_ciclo'] > 1
    else f"C{row['ano']-1}52",  # Assumindo 52 ciclos por ano
    axis=1
)

# Remover colunas auxiliares se não precisar
df_result = df_result.drop(['ano', 'num_ciclo'], axis=1)

df_result.head()

Ciclo    PDV cod_produto pedido_id data_emissao_nf  \
0  C202507  12522       52757   1515922      2025-07-09   
1  C202507  12817       52757   1515918      2025-07-09   
2  C202507  12817       87066   1517306      2025-07-09   
3  C202507  12818       52757   1515924      2025-07-09   
4  C202507  12820       52757   1515943      2025-07-09   

                   data_pedido    data_prevista_atendimento  \
0  2025-05-22 00:00:00.0000000  2025-06-06 00:00:00.0000000   
1  2025-05-22 00:00:00.0000000  2025-06-06 00:00:00.0000000   
2  2025-05-22 00:00:00.0000000  2025-06-13 00:00:00.0000000   
3  2025-05-22 00:00:00.0000000  2025-06-06 00:00:00.0000000   
4  2025-05-22 00:00:00.0000000  2025-06-06 00:00:00.0000000   

   faturado_industria  quantidade_pedida                 status salescurve  \
0                   5                 35  Parcialmente Atendido          C   
1                  24                 90  Parcialmente Atendido          C   
2                   1                  9              Concluído          C   
3                   4                 25  Parcialmente Atendido          C   
4                   3                 20  Parcialmente Atendido          C   

   valor_total_produtos     notas     pedidos atendimento ciclo_anterior  
0                 45.36  31953127  0165202706    0.142857        C202506  
1                217.71  31754122  0165202491    0.266667        C202506  
2                  6.11  31754122  0165206643    0.111111        C202506  
3                 36.29  76077782  0165202707        0.16        C202506  
4                 27.21  29403846  0165202369        0.15        C202506

In [5]:
conn = pyodbc.connect(
    f"DRIVER={{SQL Server}};"
    f"SERVER={config['banco']['host']},1433;"
    f"DATABASE=GINSENG;"
    f"UID={config['banco']['user']};"
    f"PWD={config['banco']['password']}")

# 1. Puxa estoque zerado (já filtrado)
query_estoque = """
SELECT 
    emh.PDV,
    emh.SKU,
    cd.Ciclo ,
    COUNT(emh.data_estoque) AS QTD_dias_zerado
FROM estoque_mar_historico emh
INNER JOIN (
    SELECT DISTINCT bm.PDV
    FROM base_pdvs_marca bm
    WHERE bm.TRANSFER = 'VD'
) bpm ON emh.PDV = bpm.PDV
inner join ciclos_data_2025 cd on cd.[Date] = emh.data_estoque and cd.MARCA ='BOT'
WHERE emh.[ESTOQUE ATUAL] = 0
  AND emh.data_estoque > '2025-07-01'
  group by emh.sku, emh.PDV ,cd.Ciclo 
"""
df_estoque = pd.read_sql(query_estoque, conn)

# 3. Puxa ruptura
query_ruptura = """
SELECT 
    ciclo,
    ponto_de_venda,
    sku,
    descricao,
    categoria,
    marca,
    classe,
    fase_do_produto,
    valor_da_receita,
    valor_da_ruptura,
    percentual_da_ruptura,
    quantidade_de_ruptura,
    macro_causa
FROM ruptura
WHERE ciclo in ('202510','202511','202512','202513','202514','202515','202516','202517')
"""
df_ruptura = pd.read_sql(query_ruptura, conn)



C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_35380\1986334479.py:26: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  df_estoque = pd.read_sql(query_estoque, conn)
C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_35380\1986334479.py:47: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  df_ruptura = pd.read_sql(query_ruptura, conn)


In [6]:
conn = pyodbc.connect(
    f"DRIVER={{SQL Server}};"
    f"SERVER={config['banco']['host']},1433;"
    f"DATABASE=GINSENG;"
    f"UID={config['banco']['user']};"
    f"PWD={config['banco']['password']}")

query_criticos = """
select dh.loja_id as PDV, 
dh.code as SKU,
c.Ciclo,
count(dh.criticalitem_iscritical) as QTD_Dias_Critico
from draft_historico dh 
inner join ciclos_data_2025 c on c.[Date] = dh.[data] and c.MARCA = 'BOT'
where dh.criticalitem_iscritical = 1
group by 
dh.loja_id , 
dh.code,
c.Ciclo
"""

df_criticos = pd.read_sql(query_criticos, conn)

C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_35380\392044023.py:22: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  df_criticos = pd.read_sql(query_criticos, conn)


In [7]:
df_estoque.columns

Index(['PDV', 'SKU', 'Ciclo', 'QTD_dias_zerado'], dtype='object')

In [8]:

# ---- Ajuste de ciclo ----
# Ciclo de df_estoque está no formato "Cxxxx" (tipo C202510 por exemplo)
# No SQL você removia a 1ª letra, aqui fazemos o mesmo:
df_estoque['Ciclo_clean'] = df_estoque['Ciclo'].astype(str).str[1:]

# ---- Join réplica da query SQL ----
df_final = df_ruptura.merge(
    df_estoque,
    left_on=["sku", "ponto_de_venda", "ciclo"],
    right_on=["SKU", "PDV", "Ciclo_clean"],
    how="left"
)

# ---- Ordenar igual ao SQL ----
df_final = df_final.sort_values(["ciclo", "SKU", "PDV"]).reset_index(drop=True)

df_final.head()

ciclo ponto_de_venda   sku                            descricao  \
0  202510          20998  1004        FLORATTA DES COL MY BLUE 75ml   
1  202510          24293  1004        FLORATTA DES COL MY BLUE 75ml   
2  202510          20968  1296  PMPCK THE BLEND DES ANTIT AER 2x75g   
3  202510          20969  1296  PMPCK THE BLEND DES ANTIT AER 2x75g   
4  202510          20970  1296  PMPCK THE BLEND DES ANTIT AER 2x75g   

      categoria marca classe fase_do_produto valor_da_receita  \
0    PERFUMARIA   BOT      E          Maduro                0   
1    PERFUMARIA   BOT      B          Maduro                0   
2  DESODORANTES   BOT      C          Maduro                0   
3  DESODORANTES   BOT      E          Maduro                0   
4  DESODORANTES   BOT      E          Maduro                0   

  valor_da_ruptura percentual_da_ruptura  quantidade_de_ruptura  \
0           348.56                   100                      2   
1           173.35                   100                      1   
2            84.22                   100                      1   
3            52.28                   100                      0   
4            93.43                   100                      1   

       macro_causa    PDV   SKU    Ciclo  QTD_dias_zerado Ciclo_clean  
0  Causa Indústria  20998  1004  C202510              8.0      202510  
1  Causa Indústria  24293  1004  C202510              2.0      202510  
2  Causa Indústria  20968  1296  C202510             13.0      202510  
3  Causa Indústria  20969  1296  C202510             13.0      202510  
4  Causa Indústria  20970  1296  C202510             13.0      202510

In [9]:
df_result.head()

Ciclo    PDV cod_produto pedido_id data_emissao_nf  \
0  C202507  12522       52757   1515922      2025-07-09   
1  C202507  12817       52757   1515918      2025-07-09   
2  C202507  12817       87066   1517306      2025-07-09   
3  C202507  12818       52757   1515924      2025-07-09   
4  C202507  12820       52757   1515943      2025-07-09   

                   data_pedido    data_prevista_atendimento  \
0  2025-05-22 00:00:00.0000000  2025-06-06 00:00:00.0000000   
1  2025-05-22 00:00:00.0000000  2025-06-06 00:00:00.0000000   
2  2025-05-22 00:00:00.0000000  2025-06-13 00:00:00.0000000   
3  2025-05-22 00:00:00.0000000  2025-06-06 00:00:00.0000000   
4  2025-05-22 00:00:00.0000000  2025-06-06 00:00:00.0000000   

   faturado_industria  quantidade_pedida                 status salescurve  \
0                   5                 35  Parcialmente Atendido          C   
1                  24                 90  Parcialmente Atendido          C   
2                   1                  9              Concluído          C   
3                   4                 25  Parcialmente Atendido          C   
4                   3                 20  Parcialmente Atendido          C   

   valor_total_produtos     notas     pedidos atendimento ciclo_anterior  
0                 45.36  31953127  0165202706    0.142857        C202506  
1                217.71  31754122  0165202491    0.266667        C202506  
2                  6.11  31754122  0165206643    0.111111        C202506  
3                 36.29  76077782  0165202707        0.16        C202506  
4                 27.21  29403846  0165202369        0.15        C202506

In [10]:
df_result['ciclo_anterior_tratado'] = df_result['ciclo_anterior'].str[-6:]

df_result.head()

Ciclo    PDV cod_produto pedido_id data_emissao_nf  \
0  C202507  12522       52757   1515922      2025-07-09   
1  C202507  12817       52757   1515918      2025-07-09   
2  C202507  12817       87066   1517306      2025-07-09   
3  C202507  12818       52757   1515924      2025-07-09   
4  C202507  12820       52757   1515943      2025-07-09   

                   data_pedido    data_prevista_atendimento  \
0  2025-05-22 00:00:00.0000000  2025-06-06 00:00:00.0000000   
1  2025-05-22 00:00:00.0000000  2025-06-06 00:00:00.0000000   
2  2025-05-22 00:00:00.0000000  2025-06-13 00:00:00.0000000   
3  2025-05-22 00:00:00.0000000  2025-06-06 00:00:00.0000000   
4  2025-05-22 00:00:00.0000000  2025-06-06 00:00:00.0000000   

   faturado_industria  quantidade_pedida                 status salescurve  \
0                   5                 35  Parcialmente Atendido          C   
1                  24                 90  Parcialmente Atendido          C   
2                   1                  9              Concluído          C   
3                   4                 25  Parcialmente Atendido          C   
4                   3                 20  Parcialmente Atendido          C   

   valor_total_produtos     notas     pedidos atendimento ciclo_anterior  \
0                 45.36  31953127  0165202706    0.142857        C202506   
1                217.71  31754122  0165202491    0.266667        C202506   
2                  6.11  31754122  0165206643    0.111111        C202506   
3                 36.29  76077782  0165202707        0.16        C202506   
4                 27.21  29403846  0165202369        0.15        C202506   

  ciclo_anterior_tratado  
0                 202506  
1                 202506  
2                 202506  
3                 202506  
4                 202506

In [11]:
df_contest_rupt = pd.merge(left=df_final,right=df_result,left_on= ['ciclo','ponto_de_venda','sku'],right_on=['ciclo_anterior_tratado','PDV','cod_produto'],how='left')

df_contest_rupt.shape

(231917, 35)

In [12]:

df_criticos['ano'] = df_criticos['Ciclo'].str[1:5].astype(int)
df_criticos['num_ciclo'] = df_criticos['Ciclo'].str[5:].astype(int)


df_criticos['ciclo_anterior'] = df_criticos.apply(
    lambda row: f"C{row['ano']}{row['num_ciclo']-1:02d}" if row['num_ciclo'] > 1
    else f"C{row['ano']-1}52",  # Assumindo 52 ciclos por ano
    axis=1
)

df_criticos = df_criticos.rename(columns={'Ciclo':'Critico no Ciclo','ciclo_anterior':'Critico no Ciclo Anterior' })

df_criticos.head()

PDV    SKU Critico no Ciclo  QTD_Dias_Critico   ano  num_ciclo  \
0  12817  80888          C202511                14  2025         11   
1  23156  49970          C202511                16  2025         11   
2  12522  85105          C202513                11  2025         13   
3  20989  49958          C202513                 2  2025         13   
4  23703  48785          C202515                 6  2025         15   

  Critico no Ciclo Anterior  
0                   C202510  
1                   C202510  
2                   C202512  
3                   C202512  
4                   C202514

In [13]:
df_contest_rupt['ciclo'] = "C"+df_contest_rupt['ciclo']

In [14]:
df_contest_rupt_crit = pd.merge(df_contest_rupt,df_criticos[['PDV','SKU','Critico no Ciclo']],
                                left_on=['ponto_de_venda','sku','ciclo'],
                                right_on=['PDV','SKU','Critico no Ciclo'],
                                  how='left')



In [15]:
df_contest_rupt_crit = df_contest_rupt_crit.drop(columns=['PDV_x', 'SKU_x', 'Ciclo_x','Ciclo_clean',
       'Ciclo_y', 'PDV_y', 'cod_produto','status', 'salescurve','PDV', 'SKU_y'])

df_contest_rupt_crit.columns

Index(['ciclo', 'ponto_de_venda', 'sku', 'descricao', 'categoria', 'marca',
       'classe', 'fase_do_produto', 'valor_da_receita', 'valor_da_ruptura',
       'percentual_da_ruptura', 'quantidade_de_ruptura', 'macro_causa',
       'QTD_dias_zerado', 'pedido_id', 'data_emissao_nf', 'data_pedido',
       'data_prevista_atendimento', 'faturado_industria', 'quantidade_pedida',
       'valor_total_produtos', 'notas', 'pedidos', 'atendimento',
       'ciclo_anterior', 'ciclo_anterior_tratado', 'Critico no Ciclo'],
      dtype='object')

In [16]:
df_contest_rupt_crit = pd.merge(df_contest_rupt_crit,df_criticos[['PDV','SKU','Critico no Ciclo Anterior']],
                                left_on=['ponto_de_venda','sku','ciclo'],
                                right_on=['PDV','SKU','Critico no Ciclo Anterior'],
                                  how='left')

In [17]:
df_contest_rupt_crit['ciclo'] = "C"+df_contest_rupt_crit['ciclo']

df_contest_rupt_crit.head()

ciclo ponto_de_venda   sku                            descricao  \
0  CC202510          20998  1004        FLORATTA DES COL MY BLUE 75ml   
1  CC202510          24293  1004        FLORATTA DES COL MY BLUE 75ml   
2  CC202510          20968  1296  PMPCK THE BLEND DES ANTIT AER 2x75g   
3  CC202510          20969  1296  PMPCK THE BLEND DES ANTIT AER 2x75g   
4  CC202510          20970  1296  PMPCK THE BLEND DES ANTIT AER 2x75g   

      categoria marca classe fase_do_produto valor_da_receita  \
0    PERFUMARIA   BOT      E          Maduro                0   
1    PERFUMARIA   BOT      B          Maduro                0   
2  DESODORANTES   BOT      C          Maduro                0   
3  DESODORANTES   BOT      E          Maduro                0   
4  DESODORANTES   BOT      E          Maduro                0   

  valor_da_ruptura  ... valor_total_produtos  notas pedidos  atendimento  \
0           348.56  ...                  NaN    NaN     NaN          NaN   
1           173.35  ...                  NaN    NaN     NaN          NaN   
2            84.22  ...                  NaN    NaN     NaN          NaN   
3            52.28  ...                  NaN    NaN     NaN          NaN   
4            93.43  ...                  NaN    NaN     NaN          NaN   

  ciclo_anterior ciclo_anterior_tratado Critico no Ciclo  PDV  SKU  \
0            NaN                    NaN              NaN  NaN  NaN   
1            NaN                    NaN              NaN  NaN  NaN   
2            NaN                    NaN              NaN  NaN  NaN   
3            NaN                    NaN              NaN  NaN  NaN   
4            NaN                    NaN              NaN  NaN  NaN   

   Critico no Ciclo Anterior  
0                        NaN  
1                        NaN  
2                        NaN  
3                        NaN  
4                        NaN  

[5 rows x 30 columns]

In [18]:
df_contest_rupt_crit = df_contest_rupt_crit.drop(columns=['PDV',
       'SKU','ciclo_anterior', 'ciclo_anterior_tratado'])

In [19]:
df_contest_rupt_crit['QTD_dias_zerado'] = df_contest_rupt_crit['QTD_dias_zerado'].fillna(0)

In [ ]:
df_contest_rupt_crit['causa_rpt_revisada'] = np.where((df_contest_rupt_crit['valor_da_ruptura']==0)| (df_contest_rupt_crit['QTD_dias_zerado']== 0),"Não Houve Ruptura",np.where(df_contest_rupt_crit['atendimento']< 0.86,"Causa Indústria", np.where(df_contest_rupt_crit['fase_do_produto'] == "Lançamento","Lançamento","Causa Franqueado")))

In [21]:
df_contest_rupt_crit['causa_rpt_revisada'] = np.where(df_contest_rupt_crit['macro_causa']=="Causa Franqueado",df_contest_rupt_crit['causa_rpt_revisada'],df_contest_rupt_crit['macro_causa'])

In [22]:
df_contest_rupt_crit['valor_da_ruptura'] = df_contest_rupt_crit['valor_da_ruptura'].str.replace(',','.')

df_contest_rupt_crit['valor_da_ruptura'] = df_contest_rupt_crit['valor_da_ruptura'].astype('float')

In [23]:
df_contest_rupt_crit['valor_da_receita'] = df_contest_rupt_crit['valor_da_receita'].str.replace(',','.')

df_contest_rupt_crit['valor_da_receita'] = df_contest_rupt_crit['valor_da_receita'].astype('float')

In [24]:
df_contest_rupt_crit['VALOR RPT FRANQ'] = np.where(df_contest_rupt_crit['macro_causa']=="Causa Franqueado", df_contest_rupt_crit['valor_da_ruptura'],0)

df_contest_rupt_crit['valor rpt franq revisada'] = np.where(df_contest_rupt_crit['causa_rpt_revisada']=="Causa Franqueado", df_contest_rupt_crit['valor_da_ruptura'],0)

In [25]:
df_contest_rupt_crit.to_excel(r"C:\Users\joao.herculano\Documents\test_rpt_ajustado24-10.xlsx",index=False)